In [3]:
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt 
from sklearn.datasets import load_boston
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense 
from tensorflow.keras.optimizers import Adam 

In [4]:
boston = load_boston()
df = pd.DataFrame(boston.data, columns=boston.feature_names)
df["PRICE"] = boston.target

print(df.shape)
df.head(n=10)

(506, 14)


c:\Users\lio22\AppData\Local\Programs\Python\Python38\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function load_boston is deprecated; `load_boston` is deprecated in 1.0 and will be removed in 1.2.

    The Boston housing prices dataset has an ethical problem. You can refer to
    the documentation of this function for further details.

    The scikit-learn maintainers therefore strongly discourage the use of this
    dataset unless the purpose of the code is to study and educate about
    ethical issues in data science and machine learning.

    In this special case, you can fetch the dataset from the original
    source::

        import pandas as pd
        import numpy as np


        data_url = "http://lib.stat.cmu.edu/datasets/boston"
        raw_df = pd.read_csv(data_url, sep="\s+", skiprows=22, header=None)
        data = np.hstack([raw_df.values[::2, :], raw_df.values[1::2, :2]])
        target = raw_df.values[1::2, 2]

    Alternative datasets include the

CRIM    ZN  INDUS  CHAS    NOX     RM    AGE     DIS  RAD    TAX  \
0  0.00632  18.0   2.31   0.0  0.538  6.575   65.2  4.0900  1.0  296.0   
1  0.02731   0.0   7.07   0.0  0.469  6.421   78.9  4.9671  2.0  242.0   
2  0.02729   0.0   7.07   0.0  0.469  7.185   61.1  4.9671  2.0  242.0   
3  0.03237   0.0   2.18   0.0  0.458  6.998   45.8  6.0622  3.0  222.0   
4  0.06905   0.0   2.18   0.0  0.458  7.147   54.2  6.0622  3.0  222.0   
5  0.02985   0.0   2.18   0.0  0.458  6.430   58.7  6.0622  3.0  222.0   
6  0.08829  12.5   7.87   0.0  0.524  6.012   66.6  5.5605  5.0  311.0   
7  0.14455  12.5   7.87   0.0  0.524  6.172   96.1  5.9505  5.0  311.0   
8  0.21124  12.5   7.87   0.0  0.524  5.631  100.0  6.0821  5.0  311.0   
9  0.17004  12.5   7.87   0.0  0.524  6.004   85.9  6.5921  5.0  311.0   

   PTRATIO       B  LSTAT  PRICE  
0     15.3  396.90   4.98   24.0  
1     17.8  396.90   9.14   21.6  
2     17.8  392.83   4.03   34.7  
3     18.7  394.63   2.94   33.4  
4     18.7  396.90   5.33   36.2  
5     18.7  394.12   5.21   28.7  
6     15.2  395.60  12.43   22.9  
7     15.2  396.90  19.15   27.1  
8     15.2  386.63  29.93   16.5  
9     15.2  386.71  17.10   18.9

In [5]:
from sklearn.preprocessing import MinMaxScaler

scaler = MinMaxScaler()
scaled_features = scaler.fit_transform(df[['RM', 'LSTAT']])

In [6]:
def get_update_weight_values_batch(bias, w1, w2, rm, lstat, target, lr=0.01):
    
    N = target.shape[0]
    print("N amount", N)
    predicted = w1 * rm  + w2 * lstat + bias 
    
    diff= target - predicted
    bias_factor = np.ones((N, ))
    
    w1_update = -(2/N)*lr*np.dot(rm.T, diff)
    w2_update = -(2/N)*lr*np.dot(lstat.T, diff)
    bias_update = -(2/N)*lr*np.dot(bias_factor.T, diff)
    
    return bias_update, w1_update, w2_update

In [7]:
batch_indicies = np.random.choice(506, 30)
print(batch_indicies)

df["RM"].values[batch_indicies]
print(df["RM"].values[batch_indicies])

[166 265 271  78 434  48 472  38 125  54 232  22 299 224 299 205 327 149
 253 137 121 368 213 461 116  26 258 441 343 316]
[7.929 5.56  6.24  6.232 6.208 5.399 6.437 5.966 5.986 5.888 8.337 6.142
 7.041 8.266 7.041 5.891 6.083 5.597 8.259 6.454 6.004 4.97  6.375 6.376
 6.176 5.813 7.333 6.406 6.696 5.914]


In [8]:
def batch_random_gradient_descent(features, target, epochs, batch_size=30, verbose=True):
    np.random.seed = 2021
    w1 = np.zeros((1, ))
    w2 = np.zeros((1, ))
    bias = np.zeros((1, ))
    print(f"first w1 : {w1} w2 : {w2} bias : {bias}")
    
    lr = 0.01
    rm = features[: , 0]
    lstat = features[:, 1]
    
    for i in range(epochs):
        
        batch_indexes = np.random.choice(target.shape[0], batch_size)
        rm_batch = rm[batch_indexes]
        lstat_batch = lstat[batch_indexes]
        target_batch = target[batch_indexes]
        
        bias_update, w1_update, w2_update = get_update_weight_values_batch(bias, w1, w2, rm_batch, lstat_batch, target_batch)
        
        w1 = w1 - w1_update
        w2 = w2 - w2_update 
        bias = bias - bias_update
        
        if verbose : 
            print("Epoch : ", i + 1, "/", epochs)
            predicted = w1 * rm + w2 * lstat + bias 
            diff = target - predicted
            mse_loss = np.mean(np.square(diff))
            print(f"w1 {w1} w2 {w2} bias {bias} loss {mse_loss}")  
    
    return w1, w2, bias 
    

In [9]:
w1, w2, bias = batch_random_gradient_descent(scaled_features, df["PRICE"].values, epochs=5000, batch_size=30, verbose=True )
print(f"fianl w1 {w1} w2 {w2} bias {bias}")
print(w1, w2, bias)

first w1 : [0.] w2 : [0.] bias : [0.]
N amount 30
Epoch :  1 / 5000
w1 [0.23841801] w2 [0.11386496] bias [0.44273333] loss 565.2975496023189
N amount 30
Epoch :  2 / 5000
w1 [0.48981583] w2 [0.22211341] bias [0.89640971] loss 538.4525347987145
N amount 30
Epoch :  3 / 5000
w1 [0.72265336] w2 [0.32822941] bias [1.32657736] loss 513.7992385007065
N amount 30
Epoch :  4 / 5000
w1 [0.97032065] w2 [0.43326096] bias [1.79269456] loss 488.05511909463127
N amount 30
Epoch :  5 / 5000
w1 [1.19264483] w2 [0.53011867] bias [2.18403883] loss 466.6516570889225
N amount 30
Epoch :  6 / 5000
w1 [1.41290985] w2 [0.63866798] bias [2.56301887] loss 446.2372776887045
N amount 30
Epoch :  7 / 5000
w1 [1.64089065] w2 [0.72814925] bias [2.95084738] loss 426.0509138497334
N amount 30
Epoch :  8 / 5000
w1 [1.83635982] w2 [0.82543263] bias [3.29876269] loss 408.47394892358966
N amount 30
Epoch :  9 / 5000
w1 [2.04666558] w2 [0.91247995] bias [3.66264848] loss 390.58148823098975
N amount 30
Epoch :  10 / 5000
w

In [10]:
predicted = scaled_features[:, 0 ]* w1 + scaled_features[:, 1] * w2 + bias 
df["PREDICTED PRICE RANDOM"] = predicted 
df.head(10)

CRIM    ZN  INDUS  CHAS    NOX     RM    AGE     DIS  RAD    TAX  \
0  0.00632  18.0   2.31   0.0  0.538  6.575   65.2  4.0900  1.0  296.0   
1  0.02731   0.0   7.07   0.0  0.469  6.421   78.9  4.9671  2.0  242.0   
2  0.02729   0.0   7.07   0.0  0.469  7.185   61.1  4.9671  2.0  242.0   
3  0.03237   0.0   2.18   0.0  0.458  6.998   45.8  6.0622  3.0  222.0   
4  0.06905   0.0   2.18   0.0  0.458  7.147   54.2  6.0622  3.0  222.0   
5  0.02985   0.0   2.18   0.0  0.458  6.430   58.7  6.0622  3.0  222.0   
6  0.08829  12.5   7.87   0.0  0.524  6.012   66.6  5.5605  5.0  311.0   
7  0.14455  12.5   7.87   0.0  0.524  6.172   96.1  5.9505  5.0  311.0   
8  0.21124  12.5   7.87   0.0  0.524  5.631  100.0  6.0821  5.0  311.0   
9  0.17004  12.5   7.87   0.0  0.524  6.004   85.9  6.5921  5.0  311.0   

   PTRATIO       B  LSTAT  PRICE  PREDICTED PRICE RANDOM  
0     15.3  396.90   4.98   24.0               28.870670  
1     17.8  396.90   9.14   21.6               25.412827  
2     17.8  392.83   4.03   34.7               32.474049  
3     18.7  394.63   2.94   33.4               32.267216  
4     18.7  396.90   5.33   36.2               31.443033  
5     18.7  394.12   5.21   28.7               28.011412  
6     15.2  395.60  12.43   22.9               21.272300  
7     15.2  396.90  19.15   27.1               17.687426  
8     15.2  386.63  29.93   16.5                8.032217  
9     15.2  386.71  17.10   18.9               18.197604

In [11]:
for batch_step in range(0, 506, 30):
    print(batch_step)

0
30
60
90
120
150
180
210
240
270
300
330
360
390
420
450
480


In [12]:
def batch_gradient_descent(features, target, epochs=1000, batch_size=30, verbose=True):
    
    np.random.seed = 2021
    w1 = np.zeros((1, ))
    w2 = np.zeros((1, ))
    bias = np.zeros((1, ))
    print(f"First w1 :{w1}  w2 {w2} bias {bias}")
    
    lr = 0.01
    rm = features[:, 0]
    lstat = features[:, 1]
    
    for i in range(epochs):
        for batch_step in range(0, target.shape[0], batch_size):
            rm_batch = rm[batch_step:batch_step + batch_size]
            lstat_batch = lstat[batch_step:batch_step + batch_size ]
            target_batch = target[batch_step:batch_step + batch_size]

            bias_update, w1_update, w2_update = get_update_weight_values_batch(bias, w1, w2, rm_batch, lstat_batch, target_batch, lr)
            w1 = w1 - w1_update
            w2 = w2 - w2_update 
            bias = bias - bias_update
            
            if verbose : 
                print("Epoch : ", i + 1, "/", epochs, "batch_step {batch_step}")
                predicted = w1 * rm + w2 *lstat + bias 
                diff = target - predicted
                mes_loss = np.mean(np.square(diff))
                print(f"w1 {w1} w2 {w2} bias {bias} mse_loss {mse_loss} ")

    
    return w1, w2, bias 

            

In [13]:
w1, w2, bias = batch_gradient_descent(scaled_features, df["PRICE"].values, epochs=5000, batch_size=30, verbose=True)
print("final w1, w2 bias")
print(w1, w2, bias)

First w1 :[0.]  w2 [0.] bias [0.]
N amount 30
Epoch :  1 / 5000 batch_step {batch_step}
w1 {w1} w2 {w2} bias {bias} mse_loss {mse_loss} 
N amount 30
Epoch :  1 / 5000 batch_step {batch_step}
w1 {w1} w2 {w2} bias {bias} mse_loss {mse_loss} 
N amount 30
Epoch :  1 / 5000 batch_step {batch_step}
w1 {w1} w2 {w2} bias {bias} mse_loss {mse_loss} 
N amount 30
Epoch :  1 / 5000 batch_step {batch_step}
w1 {w1} w2 {w2} bias {bias} mse_loss {mse_loss} 
N amount 30
Epoch :  1 / 5000 batch_step {batch_step}
w1 {w1} w2 {w2} bias {bias} mse_loss {mse_loss} 
N amount 30
Epoch :  1 / 5000 batch_step {batch_step}
w1 {w1} w2 {w2} bias {bias} mse_loss {mse_loss} 
N amount 30
Epoch :  1 / 5000 batch_step {batch_step}
w1 {w1} w2 {w2} bias {bias} mse_loss {mse_loss} 
N amount 30
Epoch :  1 / 5000 batch_step {batch_step}
w1 {w1} w2 {w2} bias {bias} mse_loss {mse_loss} 
N amount 30
Epoch :  1 / 5000 batch_step {batch_step}
w1 {w1} w2 {w2} bias {bias} mse_loss {mse_loss} 
N amount 30
Epoch :  1 / 5000 batch_ste

KeyboardInterrupt: 